In [60]:
from policyengine_core.model_api import *
from policyengine_us import *
from scipy.optimize import differential_evolution

INCOME_ELASTICITY = -0.05
SUBSTITUTION_ELASTICITY = 0.25

def create_funding_reform(flat_tax_rate: float, include_lsrs: bool = True):
    return Reform.from_dict({
        "gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.abolish_payroll_tax": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax": {
            "year:2023:10": True
        },
        "gov.ssa.ssi.abolish_ssi": {
            "year:2023:10": True
        },
        "gov.usda.snap.abolish_snap": {
            "year:2023:10": True
        },
        "gov.usda.wic.abolish_wic": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.rate": {
            "year:2023:10": flat_tax_rate
        },
        "gov.contrib.ubi_center.flat_tax.deduct_ptc": {
            "year:2023:10": True
        },
        "gov.usda.snap.emergency_allotment.allowed": {
            "year:2023:10": False
        },
        "simulation.reported_state_income_tax": {
            "year:2023:10": True
        },
        "gov.simulation.labor_supply_responses.income_elasticity": {
            "year:2023:10": INCOME_ELASTICITY
        } if include_lsrs else {},
        "gov.simulation.labor_supply_responses.substitution_elasticity": {
            "year:2023:10": SUBSTITUTION_ELASTICITY
        } if include_lsrs else {},
    },
    "us",
    )

def create_baseline_reform():
    return Reform.from_dict({
            "gov.usda.snap.emergency_allotment.allowed": {
                "year:2023:10": False
            },
            "simulation.reported_state_income_tax": {
                "year:2023:10": True
            },
        },
        "us",
    )

baseline = Microsimulation(reform=create_baseline_reform(), dataset="enhanced_cps_2023")

class BlankSlatePolicy:
    young_child: float = 0
    older_child: float = 0
    young_adult: float = 0
    adult: float = 0
    senior: float = 0
    flat_tax_rate: float = 0.40

    def __init__(self, flat_tax_rate: float = 0.40, year: int = 2024, include_lsrs: bool = True):
        self.baseline = baseline
        self.blank_slate_funded = Microsimulation(reform=create_funding_reform(flat_tax_rate, include_lsrs), dataset="enhanced_cps_2023")
        self.baseline.default_calculation_period = year
        self.blank_slate_funded.default_calculation_period = year
        self.df = self.create_dataframe()
        self.ubi_funding = self.get_ubi_funding()
        self.flat_tax_rate = flat_tax_rate
        self.include_lsrs = include_lsrs

    def create_dataframe(self) -> pd.DataFrame:
        age = self.baseline.calc("age").values
        df = pd.DataFrame(
            dict(
                baseline_net_income=self.baseline.calc(
                    "household_net_income"
                ).values,
                baseline_tax=self.baseline.calculate(
                    "household_tax"
                ).values,
                baseline_benefits=self.baseline.calculate(
                    "household_benefits"
                ).values,
                count_young_child=self.baseline.map_result(
                    age < 6, "person", "household"
                ),
                count_older_child=self.baseline.map_result(
                    (age >= 6) & (age < 18), "person", "household"
                ),
                count_adult=self.baseline.map_result(
                    (age >= 18) & (age < 65), "person", "household"
                ),
                count_senior=self.baseline.map_result(
                    age >= 65, "person", "household"
                ),
                count_person=self.baseline.map_result(
                    age >= 0, "person", "household"
                ),
                funded_net_income=self.blank_slate_funded.calculate(
                    "household_net_income"
                ).values,
                funded_tax=self.blank_slate_funded.calculate(
                    "household_tax"
                ).values,
                funded_benefits=self.blank_slate_funded.calculate(
                    "household_benefits"
                ).values,
                count_disabled=self.baseline.calculate("is_ssi_disabled", map_to="household").values,
                weight=self.baseline.calculate("household_weight").values,
            )
        )

        df["total_employment_income"] = self.baseline.calculate("employment_income", map_to="household").values
        return df

    def get_ubi_funding(self) -> float:
        return (
            (self.df.funded_tax - self.df.funded_benefits - self.df.baseline_tax + self.df.baseline_benefits)
            * self.df.weight
        ).sum()

    def get_senior_amount(
        self,
        young_child: float,
        older_child: float,
        adult: float,
        disabled: float,
        funding_offset: float = 0,
    ) -> float:
        return (
            self.ubi_funding + funding_offset
            - young_child * (self.df.count_young_child * self.df.weight).sum()
            - older_child * (self.df.count_older_child * self.df.weight).sum()
            - adult * (self.df.count_adult * self.df.weight).sum()
            - disabled * (self.df.count_disabled * self.df.weight).sum()
        ) / (self.df.count_senior * self.df.weight).sum()

    def mean_percentage_loss(
        self,
        young_child: float,
        older_child: float,
        adult: float,
        disabled: float,
        return_extras: bool = False
    ) -> float:
        senior_amount = self.get_senior_amount(
            young_child, older_child, adult, disabled,
        )
        final_net_income = (
            self.df.funded_net_income
            + self.df.count_young_child * young_child
            + self.df.count_older_child * older_child
            + self.df.count_adult * adult
            + self.df.count_senior * senior_amount
            + self.df.count_disabled * disabled
        )
        gain = final_net_income - self.df.baseline_net_income
        income_rel_change = final_net_income / self.df.funded_net_income - 1
        income_rel_change_c = np.clip(income_rel_change, -1, 1)
        income_effect = income_rel_change_c * self.df.total_employment_income * INCOME_ELASTICITY
        employment_income_change = income_effect
        MTR_GUESS = self.flat_tax_rate
        rough_net_income_change_from_lsr = employment_income_change * (1 - MTR_GUESS)
        rough_tax_change_from_lsr = employment_income_change * MTR_GUESS
        total_ubi_funding_change = (rough_tax_change_from_lsr * self.df.weight).sum()
        if self.include_lsrs:
            senior_amount = self.get_senior_amount(
                young_child, older_child, adult, disabled, total_ubi_funding_change
            )
        final_net_income = (
            self.df.funded_net_income
            + self.df.count_young_child * young_child
            + self.df.count_older_child * older_child
            + self.df.count_adult * adult
            + self.df.count_senior * senior_amount
            + self.df.count_disabled * disabled
        )
        gain = final_net_income - self.df.baseline_net_income + rough_net_income_change_from_lsr
        if not self.include_lsrs:
            gain = gain - rough_net_income_change_from_lsr
        absolute_loss = np.maximum(0, -gain)
        pct_loss = absolute_loss / np.maximum(100, self.df.baseline_net_income)
        average = np.average(
            pct_loss, weights=self.df.weight * self.df.count_person
        )
        if return_extras:
            return average, senior_amount, total_ubi_funding_change
        return average

    def solve(self, return_amounts: bool = False, return_loss: bool = False) -> dict:
        (
            self.young_child,
            self.older_child,
            self.adult,
            self.disabled,
        ) = differential_evolution(
            lambda x: self.mean_percentage_loss(*x),
            bounds=[(0, 30e3 * self.flat_tax_rate)] * 4,
            maxiter=int(1e2),
            seed=0,
        ).x
        _, self.senior, _ = self.mean_percentage_loss(
            self.young_child, self.older_child, self.adult, self.disabled, return_extras=True
        )
        self.reform = Reform.from_dict(
            {
                **create_funding_reform(self.flat_tax_rate).parameter_values,
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount": {
                    "year:2023:10": self.young_child
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount": {
                    "year:2023:10": self.older_child
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount": {
                    "year:2023:10": self.adult
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount": {
                    "year:2023:10": self.adult
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount": {
                    "year:2023:10": self.senior
                },
                "gov.contrib.ubi_center.basic_income.amount.person.disability": {
                    "year:2023:10": self.disabled
                },
            },
            "us",
        )
        if not return_amounts and not return_loss:
            return self.reform
        
        data = dict(reform=self.reform)

        if return_amounts:
            data["amounts"] = dict(
                young_child=self.young_child,
                older_child=self.older_child,
                adult=self.adult,
                senior=self.senior,
                disabled=self.disabled,
            )
        
        if return_loss:
            data["loss"] = self.mean_percentage_loss(
                self.young_child, self.older_child, self.adult, self.disabled
            )
        
        public_reform = Reform.from_dict(
            {
                path: value for path, value in self.reform.parameter_values.items()
                if path.startswith("gov")
            },
            "us",
        )
        data["id"] = public_reform.api_id
        data["reform"] = public_reform
        
        return data

In [23]:
policy_2024 = BlankSlatePolicy(0.29, year=2024, include_lsrs=True)
data_2024 = policy_2024.solve(return_amounts=True, return_loss=True)

In [61]:
import plotly.express as px
from policyengine_core.charts import *
from tqdm import tqdm

tax_rates = []
losses = []
api_ids = []

flat_tax_rates = [
    0.34, 0.33, 0.35, 0.32, 0.36, 0.31, 0.37, 0.30, 0.38,
]

for flat_tax_rate in np.linspace(0.2, 0.4, 21):
    if flat_tax_rate in flat_tax_rates:
        continue
    else:
        flat_tax_rates.append(flat_tax_rate)

flat_tax_rates = flat_tax_rates[::-1]

for flat_tax_rate in tqdm(flat_tax_rates):
    policy = BlankSlatePolicy(flat_tax_rate, year=2024)
    data = policy.solve(return_amounts=True, return_loss=True)
    tax_rates.append(flat_tax_rate)
    losses.append(data["loss"])
    api_ids.append(data["id"])

    print(f"Flat tax rate: {flat_tax_rate:.0%} | Loss: {data['loss']:.2%}")

df = pd.DataFrame(dict(
    flat_tax_rate=tax_rates,
    loss=losses,
    api_id=api_ids,
))

fig = px.line(
    df.sort_values("flat_tax_rate"),
    x="flat_tax_rate",
    y="loss",
)


format_fig(fig).update_traces(
    # Set color to BLUE
    line=dict(color=BLUE_PRIMARY),
).update_layout(
    title="Mean percentage loss by flat tax rate",
    xaxis_title="Flat tax rate",
    yaxis_title="Loss",
    xaxis_tickformat=".0%",
    yaxis_tickformat=".1%",
)

  5%|▍         | 1/22 [04:35<1:36:28, 275.66s/it]

Flat tax rate: 34% | Loss: 6.12%


  9%|▉         | 2/22 [08:09<1:19:49, 239.49s/it]

Flat tax rate: 33% | Loss: 5.54%


 14%|█▎        | 3/22 [12:21<1:17:39, 245.25s/it]

...

Flat tax rate: 30% | Loss: 4.98%


 95%|█████████▌| 21/22 [1:30:57<04:22, 262.72s/it]

Flat tax rate: 39% | Loss: 298.31%


100%|██████████| 22/22 [1:35:24<00:00, 260.19s/it]

Flat tax rate: 40% | Loss: 420.03%


In [66]:
df

flat_tax_rate      loss  api_id
0            0.34  0.061239   42757
1            0.33  0.055422   42758
2            0.35  0.093698   42759
3            0.32  0.053071   42760
4            0.36  0.179060   42762
5            0.31  0.051001   42764
6            0.37  0.594883   42766
7            0.30  0.049753   42767
8            0.38  1.760803   42768
9            0.20  0.122087   42769
10           0.21  0.109379   42770
11           0.22  0.097328   42771
12           0.23  0.086060   42772
13           0.24  0.076013   42773
14           0.25  0.066969   42774
15           0.26  0.059289   42775
16           0.27  0.053623   42776
17           0.28  0.050584   42777
18           0.29  0.049405   42778
19           0.30  0.049753   42779
20           0.39  2.983062   42780
21           0.40  4.200264   42781

In [49]:
from policyengine_us import Microsimulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd

data = data_2024

def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["young_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["older_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["senior"])
    parameters.gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_payroll_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.deduct_ptc.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.rate.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.29)
    parameters.gov.simulation.labor_supply_responses.income_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=-0.05)
    parameters.gov.simulation.labor_supply_responses.substitution_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.25)
    parameters.gov.ssa.ssi.abolish_ssi.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.abolish_snap.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.emergency_allotment.allowed.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=False)
    parameters.gov.usda.wic.abolish_wic.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class bs_reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)


def baseline_modify_parameters(parameters):
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class baseline_reform(Reform):
    def apply(self):
        self.modify_parameters(baseline_modify_parameters)


#baseline = Microsimulation(reform=baseline_reform, dataset="enhanced_cps_2023")
reformed = Microsimulation(reform=bs_reform, dataset="enhanced_cps_2023")

In [50]:
reform_net_position = reformed.calculate("household_tax", 2024).sum() - reformed.calculate("household_benefits", 2024).sum()
baseline_net_position = policy_2024.baseline.calculate("household_tax", 2024).sum() - policy_2024.baseline.calculate("household_benefits", 2024).sum()

In [56]:
reformed.calculate("employment_income", 2024).sum()/1e9 - policy_2024.baseline.calculate("employment_income", 2024).sum()/1e9

109.06489924822199

In [54]:
reform_net_position/1e9 - baseline_net_position/1e9

13.6065606698578

In [55]:
data

{'reform': policyengine_core.reforms.reform.Reform.from_dict.<locals>.reform,
 'amounts': {'young_child': 3628.3490320388237,
  'older_child': 3076.113012729034,
  'adult': 3682.3533934782613,
  'senior': 3184.686178990007,
  'disabled': 3145.2766090173845},
 'loss': 0.049404730897690874,
 'id': 42751}

In [51]:
reformed.calculate("basic_income", 2024).sum()/1e9

1167.0046601651231

In [52]:
bs_funded_net_position = policy_2024.blank_slate_funded.calculate("household_tax", 2024).sum() - policy_2024.blank_slate_funded.calculate("household_benefits", 2024).sum()
bs_funded_net_position/1e9 - baseline_net_position/1e9

1195.289312203191

In [53]:
simulations = [
    policy_2024.baseline,
    policy_2024.blank_slate_funded,
    reformed,
]

variables = [
    "flat_tax",
    "positive_agi",
]

for variable in variables:
    print(simulations[0].calculate(variable, 2024).sum()/1e9)
    for simulation, name in zip(simulations[1:], ["funded", "funded+UBI"]):
        difference = simulation.calculate(variable, 2024).sum()/1e9# - simulations[0].calculate(variable, 2024).sum()/1e9
        print(f"{name} {variable}: {difference:.2f} billion")

0.0
funded flat_tax: 4209.29 billion
funded+UBI flat_tax: 4195.96 billion
14339.120159602997
funded positive_agi: 14514.80 billion
funded+UBI positive_agi: 14468.84 billion


In [29]:
reform_net_position/1e9 - baseline_net_position/1e9

148.52866343721553

In [14]:
policy_2024.blank_slate_funded.calculate("household_tax").sum()/1e9 - policy_2024.blank_slate_funded.calculate("household_benefits").sum()/1e9 - policy_2024.baseline.calculate("household_tax").sum()/1e9 + policy_2024.baseline.calculate("household_benefits").sum()/1e9

1195.2893122031905

In [13]:
data_2024

{'reform': policyengine_core.reforms.reform.Reform.from_dict.<locals>.reform,
 'amounts': {'young_child': 3796.9693787325014,
  'older_child': 2799.6852762886547,
  'adult': 3910.449886241183,
  'senior': 3169.1287451556987,
  'disabled': 3708.8509442687473},
 'loss': 0.04685448037904899,
 'id': 42750}

In [16]:
from policyengine_us import Simulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd


def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3796)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=2799)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3910)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3910)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3169)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.disability.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3708)
    return parameters


class reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)

reformed = Microsimulation(reform=reform, dataset="enhanced_cps_2023")

reformed.calculate("basic_income", 2024).sum()/1e9


1212.6414145088575

In [20]:
policy_2024.get_senior_amount(3796, 2799, 3910, 3708, -10e9)

3054.1588967305065

In [10]:
policy_2024_no_lsrs = BlankSlatePolicy(0.29, year=2024, include_lsrs=False)
data_2024_no_lsrs = policy_2024_no_lsrs.solve(return_amounts=True, return_loss=True)

In [12]:
policy_2024.get_ubi_funding()

1195393200000.0

In [4]:
baseline = policy_2024.baseline
reformed = policy_2024.blank_slate_funded

baseline_net_position = baseline.calculate("household_tax").sum()/1e9 - baseline.calculate("household_benefits").sum()/1e9
reformed_net_position = reformed.calculate("household_tax").sum()/1e9 - reformed.calculate("household_benefits").sum()/1e9

budgetary_impact = reformed_net_position - baseline_net_position

In [9]:
3*330

990

In [6]:
data_2024

{'reform': policyengine_core.reforms.reform.Reform.from_dict.<locals>.reform,
 'amounts': {'young_child': 3796.9693787325014,
  'older_child': 2799.6852762886547,
  'adult': 3910.449886241183,
  'senior': 3170.7670701134143,
  'disabled': 3708.8509442687473},
 'loss': 0.046852349147862994,
 'id': 42741}

In [5]:
budgetary_impact

1195.3931298850234

In [10]:
import plotly.express as px
from policyengine_core.charts import *
from tqdm import tqdm

tax_rates = []
losses = []
api_ids = []

for flat_tax_rate in tqdm(np.linspace(0.2, 0.4, 21)):
    policy = BlankSlatePolicy(flat_tax_rate, year=2024)
    data = policy.solve(return_amounts=True, return_loss=True)
    tax_rates.append(flat_tax_rate)
    losses.append(data["loss"])
    api_ids.append(data["id"])

df = pd.DataFrame(dict(
    flat_tax_rate=tax_rates,
    loss=losses,
    api_id=api_ids,
))

fig = px.line(
    df.sort_values("flat_tax_rate"),
    x="flat_tax_rate",
    y="loss",
)


format_fig(fig).update_traces(
    # Set color to BLUE
    line=dict(color=BLUE_PRIMARY),
).update_layout(
    title="Mean percentage loss by flat tax rate",
    xaxis_title="Flat tax rate",
    yaxis_title="Loss",
    xaxis_tickformat=".0%",
    yaxis_tickformat=".1%",
)

100%|██████████| 21/21 [1:14:40<00:00, 213.35s/it]


In [ ]:
from policyengine_us import Microsimulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd


def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["young_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["older_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["young_adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["senior"])
    parameters.gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_payroll_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.deduct_ptc.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.rate.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.3)
    parameters.gov.simulation.labor_supply_responses.income_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=-0.05)
    parameters.gov.simulation.labor_supply_responses.substitution_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.25)
    parameters.gov.ssa.ssi.abolish_ssi.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.abolish_snap.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.emergency_allotment.allowed.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=False)
    parameters.gov.usda.wic.abolish_wic.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class bs_reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)


def baseline_modify_parameters(parameters):
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class baseline_reform(Reform):
    def apply(self):
        self.modify_parameters(baseline_modify_parameters)


baseline = Microsimulation(reform=baseline_reform, dataset="enhanced_cps_2023")
reformed = Microsimulation(reform=bs_reform, dataset="enhanced_cps_2023")

In [ ]:
data["reform"].api_id

42318

In [ ]:
reform_pos = reformed.calculate("household_tax").sum()/1e9 - reformed.calculate("household_benefits").sum()/1e9
baseline_pos = baseline.calculate("household_tax").sum()/1e9 - baseline.calculate("household_benefits").sum()/1e9
reform_pos - baseline_pos

-14.265113360794203

In [ ]:
policy.blank_slate_funded.calculate("household_tax").sum()/1e9 - policy.baseline.calculate("household_benefits").sum()/1e9

3082.306692309179

In [ ]:
from policyengine_us import Simulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd


def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3871.303409123619)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=2748.040844692595)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=4222.691573142556)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=4407.959357095953)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3574.607933975744)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_payroll_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.deduct_ptc.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.rate.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.3)
    parameters.gov.simulation.labor_supply_responses.income_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=-0.05)
    parameters.gov.simulation.labor_supply_responses.substitution_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.25)
    parameters.gov.ssa.ssi.abolish_ssi.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.abolish_snap.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.emergency_allotment.allowed.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=False)
    parameters.gov.usda.wic.abolish_wic.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters


class reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)


situation = {
  "families": {
    "your family": {
      "members": [
        "you"
      ]
    }
  },
  "households": {
    "your household": {
      "members": [
        "you"
      ]
    }
  },
  "marital_units": {
    "your marital unit": {
      "members": [
        "you"
      ]
    }
  },
  "people": {
    "you": {
      "age": {
        "2023": 40
      },
      "employment_income": {
        "2023": 500000
      }
    }
  },
  "spm_units": {
    "your household": {
      "members": [
        "you"
      ]
    }
  },
  "tax_units": {
    "your tax unit": {
      "members": [
        "you"
      ]
    }
  }
}

simulation = Simulation(
    reform=reform,
    situation=situation,
)

simulation.trace = True
simulation.calculate("employment_income", 2023)

array([516497.25], dtype=float32)

In [ ]:
simulation.tracer.print_computation_log(max_depth=6)

  employment_income<2023, (default)> = [516497.25]
    employment_income_before_lsr<2023, (default)> = [500000.]
    employment_income_behavioral_response<2023, (default)> = [16497.266]
      income_elasticity_lsr<2023, (default)> = [-1394.6615]
        employment_income_before_lsr<2023, (default)> = [500000.]
        relative_income_change<2023, (default)> = [0.05578646]
          household_net_income<2023, (lsr_measurement)> = [309192.34]
            household_market_income<2023, (lsr_measurement)> = [500000.]
            household_benefits<2023, (lsr_measurement)> = [4407.9595]
            household_refundable_tax_credits<2023, (lsr_measurement)> = [0.]
            household_tax_before_refundable_credits<2023, (lsr_measurement)> = [195215.62]
      substitution_elasticity_lsr<2023, (default)> = [17891.928]
        employment_income_before_lsr<2023, (default)> = [500000.]
        relative_wage_change<2023, (default)> = [0.14313543]
          marginal_tax_rate<2023, (lsr_measurement)>

In [59]:
px.bar(
    reformed.calculate("employment_income_behavioral_response", 2024).groupby(reformed.calculate("income_decile", map_to="person", period=2024)).sum()
)

In [58]:
import plotly.express as px

res = reformed.calculate("employment_income_behavioral_response", 2024)

px.histogram(
    res.clip(res.quantile(0.01), res.quantile(0.99)),
    nbins=100,
)

In [ ]:
tax_change = reformed.calculate("household_tax").sum()/1e9 - baseline.calculate("household_tax").sum()/1e9
flat_tax_revenue = reformed.calculate("flat_tax").sum()/1e9
benefit_change = reformed.calculate("household_benefits").sum()/1e9 - baseline.calculate("household_benefits").sum()/1e9
basic_income_payments = reformed.calculate("basic_income").sum()/1e9

tax_abolition_budgetary_impact = tax_change - flat_tax_revenue
benefit_abolition_budgetary_impact = -(benefit_change - basic_income_payments)

flat_tax_revenue_budgetary_impact = flat_tax_revenue
basic_income_payments_budgetary_impact = -basic_income_payments

[tax_abolition_budgetary_impact, benefit_abolition_budgetary_impact, flat_tax_revenue_budgetary_impact, basic_income_payments_budgetary_impact]

[-3236.3256686219, 206.62841945258106, 1508.9800102127294, -1315.0695297194302]